In [1]:
!nvidia-smi #checking whether GPU is working or not

Fri Aug 11 17:28:17 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.105.17   Driver Version: 525.105.17   CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   38C    P8     9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
! pip install -q transformers accelerate sentencepiece gradio datasets evaluate sacrebleu
#installing all the necessary libraries

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 23.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.2/244.2 kB 23.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 44.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 76.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 49.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 11.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.9/118.9 kB 15.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 25.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 81.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 65.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.7/65.7 kB 7.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.4/297.4 kB 34.1 MB/s eta 0:00

From the datasets download the dataset kde4(available on huggingface) which is a sample dataset for languuage translation and mention the two languages.

In [3]:
from datasets import load_dataset
raw_datasets = load_dataset("kde4", lang1="en", lang2="fr")
raw_datasets

Generating train split:   0%|          | 0/210173 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'translation'],
        num_rows: 210173
    })
})

In the original dataset we have only train set but we want both train and test sets to compare our outputs so use train_test_split function to break the dataset into two sets train and test.

In [4]:
from sklearn.model_selection import train_test_split
split_datasets= raw_datasets["train"].train_test_split(test_size=0.2, seed=20)
split_datasets

DatasetDict({
    train: Dataset({
        features: ['id', 'translation'],
        num_rows: 168138
    })
    test: Dataset({
        features: ['id', 'translation'],
        num_rows: 42035
    })
})

In [5]:
split_datasets["train"][45]["translation"]

{'en': 'If you choose the wrong settings here your articles could be unreadable or not sendable at all, so please be careful with these settings.',
 'fr': 'Si vous choisissez ici les mauvais paramètres, vos articles peuvent devenir illisibles ou vous ne pourrez pas du tout les envoyer. Veuillez donc être prudent avec ces paramètres.'}

Now we will be using a pre trained model from HuggingFace Helsinki-NLP/opus-mt-en-fr which contained the pre trained model of translation from english to french.

In [6]:
from transformers import pipeline
model="Helsinki-NLP/opus-mt-en-fr"
translator=pipeline("translation", model=model)
translator("If you choose the wrong settings here your articles could be unreadable or not sendable at all, so please be careful with these settings.")

/usr/local/lib/python3.10/dist-packages/transformers/models/marian/tokenization_marian.py:194: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


[{'translation_text': "Si vous choisissez les mauvais paramètres ici, vos articles pourraient être illisibles ou ne pas être envoyés du tout, alors s'il vous plaît soyez prudent avec ces paramètres."}]

We can see that the pre trained model itself is giving us somewhat good translation and after fien tuning it will get better.

Now use the AutoTokenizer to use the same tokenizer which is used in pre trained model on the dataset we are using.

In [7]:
from transformers import AutoTokenizer
tokenizer=AutoTokenizer.from_pretrained(model, return_tensors="pt")

In [8]:
def pre_processtext(text):
  inputs=[sample['en'] for sample in text['translation']]
  output=[sample['fr'] for sample in text['translation']]
  tokenized_text=tokenizer(inputs, text_target=output, max_length=128, truncation=True) #(text_target because if not done it will tokenize the french sentence according to english and so the labels will then not be correct)
  return tokenized_text

In [9]:
tokenized_datasets=split_datasets.map(
    pre_processtext,
    batched=True,
    remove_columns=split_datasets["train"].column_names #(to remove extra columns)
)

Map:   0%|          | 0/168138 [00:00<?, ? examples/s]

Map:   0%|          | 0/42035 [00:00<?, ? examples/s]

Now after preprocessing we have to choose a model to train and we will be using the AutoModelForSeq2SeqLM

In [10]:
from transformers import AutoModelForSeq2SeqLM
model_1= AutoModelForSeq2SeqLM.from_pretrained(model)

Data collator is also an important tool which is used for dynamic padding and adding -100 to short sentences to make it to match max length and also adding a start of sentence token which can be seen in decoder_input_ids.

In [11]:
from transformers import DataCollatorForSeq2Seq
data_collator=DataCollatorForSeq2Seq(tokenizer,model=model_1)

In [12]:
batch = data_collator([tokenized_datasets["train"][i] for i in range(1,3)])
print(batch.keys())
print(batch['labels'])
batch['decoder_input_ids']

dict_keys(['input_ids', 'attention_mask', 'labels', 'decoder_input_ids'])
tensor([[25966,    19,   540,     8,   669, 33355,    24, 11106,    37,   583,
           583,  9507, 10571,     3,    49, 19015,     3,    49,  1937,    74,
          2635,   973,   529, 13518,    74,   102,     0],
        [14743,   301,   548,     0,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100]])


tensor([[59513, 25966,    19,   540,     8,   669, 33355,    24, 11106,    37,
           583,   583,  9507, 10571,     3,    49, 19015,     3,    49,  1937,
            74,  2635,   973,   529, 13518,    74,   102],
        [59513, 14743,   301,   548,     0, 59513, 59513, 59513, 59513, 59513,
         59513, 59513, 59513, 59513, 59513, 59513, 59513, 59513, 59513, 59513,
         59513, 59513, 59513, 59513, 59513, 59513, 59513]])

For evaluating our model we will be using sacrebleu score which basically doesnt check the sentences grammatically but they see how many words are matching with each other and also penalise if the same word is coming multiple times but its not their in the original translation.

In [13]:
import evaluate
metric_evaluate= evaluate.load("sacrebleu")

In [14]:
import numpy as np

def compute_metrics(eval):
  preds, labels= eval
  if isinstance(preds, tuple):
    preds=preds[0]
  decoded_preds= tokenizer.batch_decode(preds, skip_special_tokens=True)

  labels=np.where(labels !=100, labels,tokenizer.pad_token_id)
  decoded_labels=tokenizer.batch_decode(labels, skip_special_tokens=True)

  decoded_preds=[pred.strip() for pred in decoded_preds]
  decoded_labels=[[label.strip()] for label in decoded_labels]

  result=metric_evaluate.compute(predictions=decoded_preds, references=decoded_labels)
  return {"bleu": result["score"]}


I will be storing my model in hugging face repository so login to HuggingFace

In [15]:
from huggingface_hub import notebook_login
notebook_login()

Now to fine tune or to train our dataset using pre trained model we will be using the Seq2SeqTrainingArguments and Seq2SeqTrainer with corresponding parameetrs which we can change to check the correctness of the model.

In [16]:
from transformers import Seq2SeqTrainingArguments

arg= Seq2SeqTrainingArguments(
    f"model-en-to-fr",
    evaluation_strategy="no",
    save_strategy="epoch",
    learning_rate=3e-5,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=64,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=3,
    predict_with_generate=True,
    fp16=True,
    push_to_hub=True #(for saving my model onto huggingface repository)
)

In [17]:
from transformers import Seq2SeqTrainer

trainer= Seq2SeqTrainer(
    model_1,
    arg,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["test"],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

Cloning https://huggingface.co./suyash2102/model-en-to-fr into local empty directory.


Download file pytorch_model.bin:   0%|          | 15.0k/285M [00:00<?, ?B/s]

Download file training_args.bin: 100%|##########| 4.00k/4.00k [00:00<?, ?B/s]

Download file runs/Aug10_17-02-45_62ab58bc436f/events.out.tfevents.1691690900.62ab58bc436f.2824.0: 100%|######…

Download file target.spm:   0%|          | 1.40k/784k [00:00<?, ?B/s]

...

Download file source.spm:   1%|          | 7.39k/760k [00:00<?, ?B/s]

Clean file runs/Aug10_17-02-45_62ab58bc436f/events.out.tfevents.1691690900.62ab58bc436f.2824.0:  10%|9        …

Clean file target.spm:   0%|          | 1.00k/784k [00:00<?, ?B/s]

Clean file source.spm:   0%|          | 1.00k/760k [00:00<?, ?B/s]

Clean file pytorch_model.bin:   0%|          | 1.00k/285M [00:00<?, ?B/s]

In [ ]:
trainer.evaluate(max_length=128) #(to check the result of pre trained model)

{'eval_loss': 1.7014496326446533,
 'eval_bleu': 3.3440279108838085e-10,
 'eval_runtime': 3279.3875,
 'eval_samples_per_second': 12.818,
 'eval_steps_per_second': 0.2}

In [ ]:
trainer.train() #(training starts form here)

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


Adding files tracked by Git LFS: ['source.spm', 'target.spm']. This may take a bit of time if the files are large.


TrainOutput(global_step=15765, training_loss=0.9015377220107834, metrics={'train_runtime': 3193.6923, 'train_samples_per_second': 157.941, 'train_steps_per_second': 4.936, 'total_flos': 1.010803691225088e+16, 'train_loss': 0.9015377220107834, 'epoch': 3.0})

In [ ]:
trainer.push_to_hub(tags="translation", commit_message="Training complete") #(to save the latest model onto the repository)

Upload file runs/Aug10_17-02-45_62ab58bc436f/events.out.tfevents.1691690900.62ab58bc436f.2824.0: 100%|########…

To https://huggingface.co./suyash2102/model-en-to-fr
   c84f9fd..3136673  main -> main

   c84f9fd..3136673  main -> main

To https://huggingface.co./suyash2102/model-en-to-fr
   3136673..33ad6ee  main -> main

   3136673..33ad6ee  main -> main



'https://huggingface.co./suyash2102/model-en-to-fr/commit/3136673dafde7fadc3597569996d6f156b3dfee1'

In [18]:
trainer.evaluate(max_length=128) #(to check after training what si the beluscore)

{'eval_loss': 1.7014496326446533,
 'eval_bleu': 3.3440279108838085e-10,
 'eval_runtime': 3256.7586,
 'eval_samples_per_second': 12.907,
 'eval_steps_per_second': 0.202}

Now to make a user interactive platform for language translation we will be using Gradio. I have uploaded a gradio_LT.py file on repo to use the gradio interface directly just by running the file.